In [114]:
import sys
from datetime import datetime

import gymnasium as gym
import numpy as np
import wandb
from stable_baselines3 import *
from stable_baselines3.common.callbacks import CallbackList
from stable_baselines3.common.logger import HumanOutputFormat
from stable_baselines3.common.logger import Logger as SB3Logger
from stable_baselines3.common.monitor import Monitor

import sinergym
import sinergym.utils.gcloud as gcloud
from sinergym.utils.callbacks import *
from sinergym.utils.constants import *
from sinergym.utils.logger import CSVLogger, WandBOutputFormat
from sinergym.utils.rewards import *
from sinergym.utils.wrappers import *

In [115]:
# Environment ID
environment = "Eplus-small_office-cool-discrete-stochastic-v1"
# Training episodes
episodes = 10
#Name of the experiment
experiment_date = datetime.today().strftime('%Y-%m-%d_%H:%M')
experiment_name = 'SB3_PPO-' + environment + \
    '-episodes-' + str(episodes) + "_7"
experiment_name += '_' + experiment_date

In [116]:
# Create wandb.config object in order to log all experiment params
experiment_params = {
    'sinergym-version': sinergym.__version__,
    'python-version': sys.version
}
experiment_params.update({'environment':environment,
                          'episodes':episodes,
                          'algorithm':'SB3-PPO'})

# Get wandb init params (you have to specify your own project and entity)
wandb_params = {"project": 'sinergym',
                "entity": 'Huron-Yin'}

print('Experiment name:', experiment_params)



Experiment name: {'sinergym-version': '3.2.7', 'python-version': '3.10.12 (main, Nov 20 2023, 15:14:05) [GCC 11.4.0]', 'environment': 'Eplus-small_office-cool-discrete-stochastic-v1', 'episodes': 10, 'algorithm': 'SB3-PPO'}


In [117]:
# Init wandb entry
run = wandb.init(
    name=experiment_name + '_' + wandb.util.generate_id(),
    config=experiment_params,
    ** wandb_params
)

print(wandb.config)

{'sinergym-version': '3.2.7', 'python-version': '3.10.12 (main, Nov 20 2023, 15:14:05) [GCC 11.4.0]', 'environment': 'Eplus-small_office-cool-discrete-stochastic-v1', 'episodes': 10, 'algorithm': 'SB3-PPO'}


In [118]:
env = gym.make(environment, env_name=experiment_name)
eval_env = gym.make(environment, env_name=experiment_name+'_EVALUATION')

#==============================================================================================#
[ENVIRONMENT] (INFO) : Creating Gymnasium environment... [SB3_PPO-Eplus-small_office-cool-discrete-stochastic-v1-episodes-10_7_2024-04-16_05:34]
#==============================================================================================#
[MODELING] (INFO) : Experiment working directory created [/workspaces/sinergym/Eplus-env-SB3_PPO-Eplus-small_office-cool-discrete-stochastic-v1-episodes-10_7_2024-04-16_05:34-res35041]
[MODELING] (INFO) : Model Config is correct.
[MODELING] (INFO) : Updated building model with whole Output:Variable available names
[MODELING] (INFO) : Updated building model with whole Output:Meter available names
[MODELING] (INFO) : runperiod established: {'start_day': 1, 'start_month': 1, 'start_year': 1991, 'end_day': 31, 'end_month': 12, 'end_year': 1991, 'start_weekday': 0, 'n_steps_per_hour': 4}
[MODELING] (INFO) : Episode length (seconds): 31536000.0
[MODELING] (IN

In [119]:
env = LoggerWrapper(env)
eval_env = LoggerWrapper(eval_env)

[WRAPPER LoggerWrapper] (INFO) : Wrapper initialized.
[WRAPPER LoggerWrapper] (INFO) : Wrapper initialized.


In [120]:
#model = DQN('MlpPolicy', env, verbose=1)
# model = PPO('MlpPolicy', env, verbose=1)

# model = PPO('MlpPolicy', env, learning_rate=0.0003, n_steps=2048, batch_size=64, n_epochs=10, gamma=0.99,
#             gae_lambda=0.95, clip_range=0.2, ent_coef=0, vf_coef=0.5, max_grad_norm=0.5, verbose=1, seed=3,
#             tensorboard_log=None)

# model = PPO('MlpPolicy', env, learning_rate=0.001, n_steps=4096, batch_size=128, n_epochs=15, gamma=0.9,
#             gae_lambda=0.9, clip_range=0.2, ent_coef=0, vf_coef=0.5, max_grad_norm=0.5, verbose=1, seed=3,
#             tensorboard_log=None)   #1
model = PPO('MlpPolicy', env, learning_rate=0.0003, n_steps=2048, batch_size=64, n_epochs=10, gamma=0.99,
            gae_lambda=0.95, clip_range=0.2, ent_coef=0, vf_coef=0.5, max_grad_norm=0.5, verbose=1, seed=3,
            tensorboard_log=None)   #2
# model = PPO('MlpPolicy', env, learning_rate=0.0003, n_steps=2048, batch_size=128, n_epochs=10, gamma=0.99,
#             gae_lambda=0.95, clip_range=0.2, ent_coef=0, vf_coef=0.5, max_grad_norm=0.5, verbose=1, seed=3,
#             tensorboard_log=None)   #3
# model = PPO('MlpPolicy', env, learning_rate=0.0003, n_steps=4096, batch_size=128, n_epochs=10, gamma=0.99,
#             gae_lambda=0.95, clip_range=0.2, ent_coef=0, vf_coef=0.5, max_grad_norm=0.5, verbose=1, seed=3,
#             tensorboard_log=None)   #4
# model = PPO('MlpPolicy', env, learning_rate=0.001, n_steps=2048, batch_size=64, n_epochs=10, gamma=0.99,
#             gae_lambda=0.95, clip_range=0.2, ent_coef=0, vf_coef=0.5, max_grad_norm=0.5, verbose=1, seed=3,
#             tensorboard_log=None)   #5
# model = PPO('MlpPolicy', env, learning_rate=0.01, n_steps=2048, batch_size=64, n_epochs=10, gamma=0.99,
#             gae_lambda=0.95, clip_range=0.2, ent_coef=0, vf_coef=0.5, max_grad_norm=0.5, verbose=1, seed=3,
#             tensorboard_log=None)   #6
model = PPO('MlpPolicy', env, learning_rate=0.0003, n_steps=4096, batch_size=64, n_epochs=10, gamma=0.99,
            gae_lambda=0.95, clip_range=0.2, ent_coef=0, vf_coef=0.5, max_grad_norm=0.5, verbose=1, seed=3,
            tensorboard_log=None)   #7


Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


In [121]:
callbacks = []

# Set up Evaluation and saving best model
eval_callback = LoggerEvalCallback(
    eval_env,
    best_model_save_path=eval_env.get_wrapper_attr('workspace_path') +
    '/best_model/',
    log_path=eval_env.get_wrapper_attr('workspace_path') +
    '/best_model/',
    eval_freq=(eval_env.get_wrapper_attr('timestep_per_episode') - 1) * 2 - 1,
    deterministic=True,
    render=False,
    n_eval_episodes=1)
callbacks.append(eval_callback)


In [122]:
# wandb logger and setting in SB3
logger = SB3Logger(
    folder=None,
    output_formats=[
        HumanOutputFormat(
            sys.stdout,
            max_length=120),
        WandBOutputFormat()])
model.set_logger(logger)
# Append callback
log_callback = LoggerCallback()
callbacks.append(log_callback)


callback = CallbackList(callbacks)

In [123]:
timesteps = episodes * (env.get_wrapper_attr('timestep_per_episode') - 1)
print(timesteps)

350390


In [124]:
model.learn(
    total_timesteps=timesteps,
    callback=callback,
    log_interval=1)

#----------------------------------------------------------------------------------------------#
[ENVIRONMENT] (INFO) : Starting a new episode... [SB3_PPO-Eplus-small_office-cool-discrete-stochastic-v1-episodes-10_7_2024-04-16_05:34] [Episode 1]
#----------------------------------------------------------------------------------------------#
[MODELING] (INFO) : Episode directory created [/workspaces/sinergym/Eplus-env-SB3_PPO-Eplus-small_office-cool-discrete-stochastic-v1-episodes-10_7_2024-04-16_05:34-res35041/Eplus-env-sub_run1]
[MODELING] (INFO) : Weather file CAN_YT_Whitehorse.719640_CWEC.epw used.
[MODELING] (INFO) : Adapting weather to building model. [CAN_YT_Whitehorse.719640_CWEC.epw]
[ENVIRONMENT] (INFO) : Saving episode output path... [/workspaces/sinergym/Eplus-env-SB3_PPO-Eplus-small_office-cool-discrete-stochastic-v1-episodes-10_7_2024-04-16_05:34-res35041/Eplus-env-sub_run1/output]


/usr/local/lib/python3.10/dist-packages/opyplus/weather_data/weather_data.py:493: FutureWarning: the 'line_terminator'' keyword is deprecated, use 'lineterminator' instead.
  epw_content = self._headers_to_epw(use_datetimes=use_datetimes) + df.to_csv(


[SIMULATOR] (INFO) : Running EnergyPlus with args: ['-w', '/workspaces/sinergym/Eplus-env-SB3_PPO-Eplus-small_office-cool-discrete-stochastic-v1-episodes-10_7_2024-04-16_05:34-res35041/Eplus-env-sub_run1/CAN_YT_Whitehorse.719640_CWEC_Random_1.0_0.0_0.001.epw', '-d', '/workspaces/sinergym/Eplus-env-SB3_PPO-Eplus-small_office-cool-discrete-stochastic-v1-episodes-10_7_2024-04-16_05:34-res35041/Eplus-env-sub_run1/output', '/workspaces/sinergym/Eplus-env-SB3_PPO-Eplus-small_office-cool-discrete-stochastic-v1-episodes-10_7_2024-04-16_05:34-res35041/Eplus-env-sub_run1/ASHRAE901_OfficeSmall_STD2019_Denver.epJSON']
[ENVIRONMENT] (INFO) : Episode 1 started.
[SIMULATOR] (INFO) : handlers initialized.
[SIMULATOR] (INFO) : handlers are ready.
[SIMULATOR] (INFO) : System is ready.
[WRAPPER LoggerWrapper] (INFO) : Creating monitor.csv for current episode (episode 1) if logger is active
--------------------------------------------------------------------------------------------------------------| 1%
|

/workspaces/sinergym/sinergym/utils/callbacks.py:309: UserWarning: Training and eval env are not of the same type<stable_baselines3.common.vec_env.dummy_vec_env.DummyVecEnv object at 0x7f926ee72530> != <LoggerWrapper<DiscretizeEnv<OrderEnforcing<PassiveEnvChecker<EplusEnv<Eplus-small_office-cool-discrete-stochastic-v1>>>>>>
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/gymnasium/spaces/box.py:240: UserWarning: WARN: Casting input x to numpy array.
  gym.logger.warn("Casting input x to numpy array.")
/usr/local/lib/python3.10/dist-packages/gymnasium/core.py:311: UserWarning: WARN: env.observation_variables to get variables from other wrappers is deprecated and will be removed in v1.0, to get this variable you can do `env.unwrapped.observation_variables` for environment variables or `env.get_wrapper_attr('observation_variables')` that will search the reminding wrappers.
  logger.warn(
/usr/local/lib/python3.10/dist-packages/gymnasium/core.py:311: UserWarning: WARN: env.action_

--------------------------------------------------------------------------------------------------------------| 1%
| action_network/                   |           |
|    index                          | 9         |
| action_simulation/                |           |
|    Cooling_Setpoint_RL            | 22.5      |
|    Heating_Setpoint_RL            | 21        |
| observation/                      |           |
|    HVAC_electricity_demand_rate   | 1925.3821 |
|    clg_setpoint                   | 22.5      |
|    core_zn_air_humidity           | 22.577223 |
|    core_zn_air_temperature        | 20.945555 |
|    core_zn_people_occupant        | 0.0       |
|    day_of_month                   | 3.0       |
|    diffuse_solar_radiation        | 0.0       |
|    direct_solar_radiation         | 0.0       |
|    hour                           | 1.0       |
|    htg_setpoint                   | 21.0      |
|    month                          | 1.0       |
|    outdoor_humidity              

...

Progress: |***************************************************************************************************| 99%
[WRAPPER LoggerWrapper] (INFO) : End of episode, recording summary (progress.csv) if logger is active
[ENVIRONMENT] (INFO) : Environment closed. [SB3_PPO-Eplus-small_office-cool-discrete-stochastic-v1-episodes-10_7_2024-04-16_05:34_EVALUATION]
#----------------------------------------------------------------------------------------------#
[ENVIRONMENT] (INFO) : Starting a new episode... [SB3_PPO-Eplus-small_office-cool-discrete-stochastic-v1-episodes-10_7_2024-04-16_05:34] [Episode 11]
#----------------------------------------------------------------------------------------------#
[MODELING] (INFO) : Episode directory created [/workspaces/sinergym/Eplus-env-SB3_PPO-Eplus-small_office-cool-discrete-stochastic-v1-episodes-10_7_2024-04-16_05:34-res35041/Eplus-env-sub_run11]
[MODELING] (INFO) : Weather file CAN_YT_Whitehorse.719640_CWEC.epw used.
[MODELING] (INFO) : Adapting 

/usr/local/lib/python3.10/dist-packages/opyplus/weather_data/weather_data.py:493: FutureWarning: the 'line_terminator'' keyword is deprecated, use 'lineterminator' instead.
  epw_content = self._headers_to_epw(use_datetimes=use_datetimes) + df.to_csv(


[WRAPPER LoggerWrapper] (INFO) : Creating monitor.csv for current episode (episode 11) if logger is active
Eval num_timesteps=350385, episode_reward=-17007.15 +/- 0.00
Episode length: 35040.00 +/- 0.00
-------------------------------------------------------
| action_network/                        |            |
|    index                               | 7          |
| action_simulation/                     |            |
|    Cooling_Setpoint_RL                 | 23         |
|    Heating_Setpoint_RL                 | 22         |
| eval/                                  |            |
|    comfort_violation(%)                | 29.3       |
|    cumulative_absolute_comfort_penalty | -2.63e+04  |
|    cumulative_absolute_energy_penalty  | -7.73e+07  |
|    cumulative_power_demand             | 7.73e+07   |
|    cumulative_reward                   | -1.7e+04   |
|    cumulative_reward_comfort_term      | -1.31e+04  |
|    cumulative_reward_energy_term       | -3.86e+03  |
|    cumulativ

/usr/local/lib/python3.10/dist-packages/gymnasium/core.py:311: UserWarning: WARN: env.observation_variables to get variables from other wrappers is deprecated and will be removed in v1.0, to get this variable you can do `env.unwrapped.observation_variables` for environment variables or `env.get_wrapper_attr('observation_variables')` that will search the reminding wrappers.
  logger.warn(
/usr/local/lib/python3.10/dist-packages/gymnasium/core.py:311: UserWarning: WARN: env.action_variables to get variables from other wrappers is deprecated and will be removed in v1.0, to get this variable you can do `env.unwrapped.action_variables` for environment variables or `env.get_wrapper_attr('action_variables')` that will search the reminding wrappers.
  logger.warn(
/usr/local/lib/python3.10/dist-packages/gymnasium/core.py:311: UserWarning: WARN: env.is_discrete to get variables from other wrappers is deprecated and will be removed in v1.0, to get this variable you can do `env.unwrapped.is_discr

[SIMULATOR] (INFO) : handlers are ready.
[SIMULATOR] (INFO) : System is ready.
-------------------------------------------------
| action_network/                   |           |
|    index                          | 7         |
| action_simulation/                |           |
|    Cooling_Setpoint_RL            | 23        |
|    Heating_Setpoint_RL            | 22        |
| observation/                      |           |
|    HVAC_electricity_demand_rate   | 5720.277  |
|    clg_setpoint                   | 23.0      |
|    core_zn_air_humidity           | 5.315053  |
|    core_zn_air_temperature        | 18.768671 |
|    core_zn_people_occupant        | 0.0       |
|    day_of_month                   | 1.0       |
|    diffuse_solar_radiation        | 0.0       |
|    direct_solar_radiation         | 0.0       |
|    hour                           | 3.0       |
|    htg_setpoint                   | 22.0      |
|    month                          | 1.0       |
|    outdoor_humidity

In [125]:
model.save(str(env.get_wrapper_attr('timestep_per_episode'))+ '/' + experiment_name)

In [126]:
env.close()

[WRAPPER LoggerWrapper] (INFO) : End of episode, recording summary (progress.csv) if logger is active
[ENVIRONMENT] (INFO) : Environment closed. [SB3_PPO-Eplus-small_office-cool-discrete-stochastic-v1-episodes-10_7_2024-04-16_05:34]


Progress: |***************************************************************************************************| 99%


In [127]:
artifact = wandb.Artifact(
        name="experiment1",
        type="training")
artifact.add_dir(
        env.get_wrapper_attr('workspace_path'),
        name='training_output/')
artifact.add_dir(
    eval_env.get_wrapper_attr('workspace_path'),
    name='evaluation_output/')
run.log_artifact(artifact)

# wandb has finished
run.finish()

wandb: Adding directory to artifact (/workspaces/sinergym/Eplus-env-SB3_PPO-Eplus-small_office-cool-discrete-stochastic-v1-episodes-10_7_2024-04-16_05:34-res35041)... Done. 1.8s
wandb: Adding directory to artifact (/workspaces/sinergym/Eplus-env-SB3_PPO-Eplus-small_office-cool-discrete-stochastic-v1-episodes-10_7_2024-04-16_05:34_EVALUATION-res35041)... Done. 1.2s
